# Handcrafted models
This notebook explores how far you can get with a simple model using good features.
Features are handpicked based on feature_engineerging_v2 and features_tsfresh.

In [1]:
import matplotlib.pyplot as plt
import pandas as pd
import gc
import numpy as np
from matplotlib import pyplot as plt
from tqdm.notebook import tqdm
import seaborn as sns
import plotly.express as px
from tqdm.notebook import tqdm

## Load data with selected features

In [2]:
features_long_timescale = [
    'abs_diff_clip_anglez_skew_1000', 'abs_diff_clip_anglez_mean_1000', 'abs_diff_clip_anglez_kurt_1000', 'abs_diff_anglez_kurt_1000', 'abs_diff_clip_anglez_skew_360', 'abs_diff_clip_anglez_median_360', 'enmo_mean_1000', 'enmo_std_360', 'abs_diff_clip_anglez_std_360', 'enmo_mean_360', 'enmo_max_1000', 'hour_stat', 'abs_diff_clip_anglez_median_12', 'abs_diff_clip_anglez_min_12', 'abs_diff_anglez_skew_360', 'enmo_std_12', 'abs_diff_anglez_std_360', 'abs_diff_clip_anglez', 'abs_diff_anglez', 'enmo_median_1000', 'sin_anglez_std_12', 'abs_diff_clip_anglez_max_12', 'abs_diff_anglez_max_12', 'enmo_mean_12', 'abs_diff_clip_anglez_min_360', 'enmo', 'hour', 'abs_diff_clip_anglez_skew_12', 'abs_diff_clip_anglez_min_1000', 'enmo_skew_12', 'sin_anglez_min_360', 'enmo_min_12', 'sin_anglez_min_1000', 'sin_anglez_std_1000', 'abs_diff_anglez_max_360', 'enmo_kurt_360', 'abs_diff_anglez_kurt_12', 'sin_anglez_min_12', 'enmo_skew_360', 'enmo_kurt_1000', 'sin_anglez_max_12', 'sin_anglez_max_360', 'abs_diff_anglez_skew_12', 'abs_diff_clip_anglez_max_360', 'abs_diff_anglez_max_1000', 'sin_anglez_std_360', 'sin_anglez_skew_12', 'sin_anglez_median_1000', 'enmo_kurt_12', 'sin_anglez_median_360', 'sin_anglez_max_1000', 'sin_anglez_mean_12', 'abs_diff_clip_anglez_max_1000', 'abs_diff_anglez_kurt_360', 'sin_anglez_skew_1000', 'minute', 'sin_anglez_kurt_360', 'enmo_min_1000', 'enmo_min_360', 'sin_anglez_skew_360', 'sin_anglez_kurt_1000', 'abs_diff_clip_anglez_kurt_12'
] 

features_short_timescale = [
    'abs_diff_clip_anglez_mean_12', 'abs_diff_anglez_max_12', 'abs_diff_clip_anglez_max_12', 'enmo_std_12', 'abs_diff_clip_anglez_median_360', 'abs_diff_anglez_median_12', 'abs_diff_clip_anglez_mean_360', 'abs_diff_clip_anglez_skew_360', 'abs_diff_anglez', 'abs_diff_clip_anglez_kurt_360', 'enmo_mean_12', 'abs_diff_anglez_median_1000', 'abs_diff_clip_anglez_min_12', 'abs_diff_anglez_kurt_360', 'enmo', 'abs_diff_anglez_std_360', 'enmo_mean_360', 'enmo_skew_12', 'enmo_median_360', 'abs_diff_clip_anglez_mean_1000', 'enmo_std_360', 'sin_anglez_kurt_360', 'abs_diff_clip_anglez_skew_1000', 'abs_diff_clip_anglez_kurt_1000', 'enmo_skew_360', 'abs_diff_anglez_kurt_12', 'sin_anglez_min_12', 'enmo_max_360', 'abs_diff_anglez_kurt_1000', 'abs_diff_clip_anglez_skew_12', 'enmo_median_1000', 'sin_anglez_std_360', 'sin_anglez_max_12', 'abs_diff_anglez_std_1000', 'enmo_mean_1000', 'abs_diff_anglez_max_360', 'enmo_min_12', 'sin_anglez_min_360', 'sin_anglez_max_360', 'enmo_std_1000', 'enmo_max_1000', 'sin_anglez_kurt_1000', 'hour_stat', 'enmo_skew_1000', 'enmo_min_360', 'sin_anglez', 'hour', 'sin_anglez_skew_12', 'sin_anglez_min_1000', 'sin_anglez_max_1000', 'abs_diff_clip_anglez_kurt_12', 'sin_anglez_median_360', 'abs_diff_anglez_max_1000', 'sin_anglez_std_1000', 'sin_anglez_median_1000', 'abs_diff_clip_anglez_max_360', 'enmo_min_1000', 'abs_diff_anglez_min_1000', 'abs_diff_anglez_min_360', 'sin_anglez_skew_1000', 'minute', 'sin_anglez_skew_360', 'enmo_kurt_12'
]

In [3]:
info_columns = ['series_id', 'target']
my_selection = [
    'abs_diff_clip_anglez_skew_1000', # best auroc for long timescale
    'abs_diff_clip_anglez_mean_1000', 
    'enmo_mean_1000',
    
    'abs_diff_clip_anglez_mean_12', # best auroc for short timescale    
    'abs_diff_clip_anglez_median_360', # most important feature for short timescale
    'sin_anglez_median_360', # 2nd most important feature for short timescale
    'abs_diff_anglez_max_12',
    'enmo_std_12',
    
    # others
    'hour_stat',
    'minute'
]

In [4]:
data = pd.read_parquet('../../../data/processed/Zzzs_train_features.parquet')

In [5]:
# convert each fp64 column to float32
cols_64 = data.select_dtypes('float64').columns
for col in cols_64:
    data[col] = data[col].astype('float32')
gc.collect()

0

In [6]:
data.head(10)

series_id  step                 timestamp     anglez    enmo  target  \
0  08db4255286f     0  2018-11-05T10:00:00-0400 -30.845301  0.0447       1   
1  08db4255286f     1  2018-11-05T10:00:05-0400 -34.181801  0.0443       1   
2  08db4255286f     2  2018-11-05T10:00:10-0400 -33.877102  0.0483       1   
3  08db4255286f     3  2018-11-05T10:00:15-0400 -34.282101  0.0680       1   
4  08db4255286f     4  2018-11-05T10:00:20-0400 -34.385799  0.0768       1   
5  08db4255286f     5  2018-11-05T10:00:25-0400 -34.925598  0.0511       1   
6  08db4255286f     6  2018-11-05T10:00:30-0400 -30.513399  0.1073       1   
7  08db4255286f     7  2018-11-05T10:00:35-0400 -30.509399  0.0649       1   
8  08db4255286f     8  2018-11-05T10:00:40-0400 -32.880600  0.0485       1   
9  08db4255286f     9  2018-11-05T10:00:45-0400 -34.674999  0.0462       1   

   train  abs_diff_anglez  abs_diff_clip_anglez  sin_anglez  ...  \
0   True         0.000000              0.000000   -0.512722  ...   
1   True         3.336500              3.336500   -0.561821  ...   
2   True         0.304699              0.304699   -0.557413  ...   
3   True         0.404999              0.404999   -0.563268  ...   
4   True         0.103699              0.103699   -0.564762  ...   
5   True         0.539799              0.539799   -0.572512  ...   
6   True         4.412199              4.412199   -0.507740  ...   
7   True         0.004000              0.004000   -0.507680  ...   
8   True         2.371201              2.371201   -0.542890  ...   
9   True         1.794399              1.794399   -0.568921  ...   

   sin_anglez_kurt_36  sin_anglez_kurt_360  sin_anglez_kurt_500  \
0            0.372967            -0.230632             0.077594   
1            0.372967            -0.230632             0.077594   
2            0.372967            -0.230632             0.077594   
3            0.372967            -0.230632             0.077594   
4            0.372967            -0.230632             0.077594   
5            0.372967            -0.230632             0.077594   
6            0.372967            -0.230632             0.077594   
7            0.372967            -0.230632             0.077594   
8            0.372967            -0.230632             0.077594   
9            0.372967            -0.230632             0.077594   

   sin_anglez_kurt_1000  abs_diff_clip_anglez_kurt_6  \
0             -0.232866                     5.505214   
1             -0.232866                     5.505214   
2             -0.232866                     5.505214   
3             -0.232866                     5.505214   
4             -0.232866                    -1.029497   
5             -0.232866                     5.726478   
6             -0.232866                     1.229628   
7             -0.232866                     0.435508   
8             -0.232866                     0.354977   
9             -0.232866                     1.060221   

   abs_diff_clip_anglez_kurt_12  abs_diff_clip_anglez_kurt_36  \
0                     -0.120555                      0.313125   
1                     -0.120555                      0.313125   
2                     -0.120555                      0.313125   
3                     -0.120555                      0.313125   
4                     -0.120555                      0.313125   
5                     -0.120555                      0.313125   
6                     -0.120555                      0.313125   
7                     -0.358268                      0.313125   
8                      1.235734                      0.313125   
9                      1.414053                      0.313125   

   abs_diff_clip_anglez_kurt_360  abs_diff_clip_anglez_kurt_500  \
0                       2.664035                       2.985674   
1                       2.664035                       2.985674   
2                       2.664035                       2.985674   
3                       2.664035                       2.98

## Transform features with a logistic regression prediction

In [7]:
from sklearn.metrics import roc_auc_score
from sklearn.linear_model import LogisticRegression

transformed_features = []
for feature in tqdm(my_selection):
    x = data[[feature]]
    y = data.target
    
    clf = LogisticRegression(random_state=0)
    clf.fit(x, y)
    
    preds = clf.predict_proba(x)[:, 1]
    auroc = roc_auc_score(y, preds)
    print(f'{feature}: {auroc}')
    if auroc > 0.7:
        name = feature+'_logres_pred'
        data[name] = preds
        transformed_features.append(name)
    gc.collect()

  0%|          | 0/10 [00:00<?, ?it/s]

abs_diff_clip_anglez_skew_1000: 0.9897042305979566
abs_diff_clip_anglez_mean_1000: 0.9897906749624402
enmo_mean_1000: 0.9683874572226683
abs_diff_clip_anglez_mean_12: 0.9535630054410761
abs_diff_clip_anglez_median_360: 0.9784204796734574
sin_anglez_median_360: 0.5428605793292275
abs_diff_anglez_max_12: 0.9131536866568979
enmo_std_12: 0.9310667914137047
hour_stat: 0.9538928677542042
minute: 0.5000164907065726


## Plot the transformed features and the target

In [19]:
# plot with plotly
display_days = 5
subsample = 12
display_set = data[:display_days*17280:subsample]
fig = px.line(display_set, x=range(len(display_set)), y=transformed_features+['target'])
fig.show()

# Train a model on the transformed features

In [9]:
# make split
X = data.drop(info_columns+['timestamp'], axis=1)
y = data.target

test_size = 0.2
sids = data.series_id.unique()
train_sids = sids[:int(len(sids)*(1-test_size))]
train_mask = data.series_id.isin(train_sids)

X_train = X[train_mask]
y_train = y[train_mask]
X_test = X[~train_mask]
y_test = y[~train_mask]

In [10]:
# set sample weights to be higher around transitions
transition = (y_train.diff().bfill() != 0)
smoothed = transition.rolling(100, center=True, min_periods=1).mean()
weight = 1 + 5*smoothed


In [11]:
gc.collect()

153

In [12]:
# train a catboost model with eval set and early stopping
from catboost import CatBoostClassifier
from sklearn.metrics import roc_auc_score

clf = CatBoostClassifier(iterations=1000, eval_metric='AUC', early_stopping_rounds=5, verbose=True)
clf.fit(X_train, y_train, eval_set=(X_test, y_test), sample_weight=weight[train_mask], verbose=True)

preds = clf.predict_proba(X_test)[:, 1]
auroc = roc_auc_score(y_test, preds)
print(f'AUROC: {auroc}')

Learning rate set to 0.313191
0:	test: 0.9924753	best: 0.9924753 (0)	total: 1.15s	remaining: 19m 7s
1:	test: 0.9936061	best: 0.9936061 (1)	total: 2.13s	remaining: 17m 43s
2:	test: 0.9946772	best: 0.9946772 (2)	total: 3.14s	remaining: 17m 24s
3:	test: 0.9950279	best: 0.9950279 (3)	total: 4.05s	remaining: 16m 47s
4:	test: 0.9955287	best: 0.9955287 (4)	total: 4.87s	remaining: 16m 8s
5:	test: 0.9956581	best: 0.9956581 (5)	total: 5.73s	remaining: 15m 48s
6:	test: 0.9957043	best: 0.9957043 (6)	total: 6.6s	remaining: 15m 36s
7:	test: 0.9959310	best: 0.9959310 (7)	total: 7.48s	remaining: 15m 27s
8:	test: 0.9959363	best: 0.9959363 (8)	total: 8.41s	remaining: 15m 26s
9:	test: 0.9958822	best: 0.9959363 (8)	total: 9.2s	remaining: 15m 10s
10:	test: 0.9959412	best: 0.9959412 (10)	total: 9.97s	remaining: 14m 56s
11:	test: 0.9959554	best: 0.9959554 (11)	total: 10.7s	remaining: 14m 43s
12:	test: 0.9959792	best: 0.9959792 (12)	total: 11.6s	remaining: 14m 40s
13:	test: 0.9959531	best: 0.9959792 (12)	tota

 0.9962716963068933 with all features

In [ ]:
display_days = 5
subsample = 10
display_set = data[:display_days*17280:subsample]
fig = px.line(display_set, x=range(len(display_set)), y=transformed_features+['target'])
fig.show()

In [13]:
# feature importances bar chart
feature_importances = pd.DataFrame({'feature': X_train.columns, 'importance': clf.feature_importances_})
feature_importances = feature_importances.sort_values('importance', ascending=False)
feature_importances['importance'] /= feature_importances['importance'].sum()

fig = px.bar(feature_importances, x='importance', y='feature', orientation='h')
fig.show()

Generate lag and lead features for the highest importance ones

In [15]:
# select the 20 highest importance features
top_features = feature_importances.feature[:20].values

offsets = [6, 36, 120]

# generate lag and lead features for each combination of feature and offset
for feature in tqdm(top_features):
    for offset in offsets:
        lag_name = f'{feature}_lag_{offset}'
        lead_name = f'{feature}_lead_{offset}'
        data[lag_name] = data[feature].shift(offset).bfill()
        data[lead_name] = data[feature].shift(-offset).ffill()
        gc.collect()

  0%|          | 0/20 [00:00<?, ?it/s]

C:\Users\EmielW\AppData\Local\Temp\ipykernel_18808\1335811270.py:11: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`

C:\Users\EmielW\AppData\Local\Temp\ipykernel_18808\1335811270.py:12: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`

C:\Users\EmielW\AppData\Local\Temp\ipykernel_18808\1335811270.py:11: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragm

Train again

In [16]:
X = data.drop(info_columns+['timestamp'], axis=1)
X_train = X[train_mask]
X_test = X[~train_mask]

clf2 = CatBoostClassifier(iterations=1000, eval_metric='AUC', early_stopping_rounds=5, verbose=True)
clf2.fit(X_train, y_train, eval_set=(X_test, y_test), sample_weight=weight[train_mask], verbose=True)

preds = clf2.predict_proba(X_test)[:, 1]
auroc = roc_auc_score(y_test, preds)
print(f'AUROC: {auroc}')

Learning rate set to 0.313191
0:	test: 0.9930662	best: 0.9930662 (0)	total: 1.28s	remaining: 21m 21s
1:	test: 0.9941525	best: 0.9941525 (1)	total: 2.52s	remaining: 20m 59s
2:	test: 0.9946808	best: 0.9946808 (2)	total: 3.8s	remaining: 21m 4s
3:	test: 0.9950208	best: 0.9950208 (3)	total: 4.95s	remaining: 20m 33s
4:	test: 0.9949496	best: 0.9950208 (3)	total: 6.11s	remaining: 20m 15s
5:	test: 0.9954448	best: 0.9954448 (5)	total: 7.1s	remaining: 19m 36s
6:	test: 0.9957659	best: 0.9957659 (6)	total: 8.43s	remaining: 19m 55s
7:	test: 0.9958663	best: 0.9958663 (7)	total: 9.37s	remaining: 19m 21s
8:	test: 0.9959346	best: 0.9959346 (8)	total: 10.3s	remaining: 18m 49s
9:	test: 0.9961406	best: 0.9961406 (9)	total: 11.4s	remaining: 18m 45s
10:	test: 0.9961701	best: 0.9961701 (10)	total: 12.4s	remaining: 18m 33s
11:	test: 0.9959352	best: 0.9961701 (10)	total: 13.6s	remaining: 18m 40s
12:	test: 0.9959483	best: 0.9961701 (10)	total: 14.6s	remaining: 18m 30s
13:	test: 0.9960036	best: 0.9961701 (10)	tot

In [17]:
# show importances again
feature_importances = pd.DataFrame({'feature': X_train.columns, 'importance': clf.feature_importances_})
feature_importances = feature_importances.sort_values('importance', ascending=False)
feature_importances['importance'] /= feature_importances['importance'].sum()

fig = px.bar(feature_importances, x='importance', y='feature', orientation='h')
fig.show()

# Plot predictions

In [ ]:
# plot with plotly detailed
display_days = 5
subsample \
    = 1
df = pd.DataFrame({'preds': preds, 'target': y_test})
df_display = df[:display_days*17280:subsample]
fig = px.line(df_display, x=range(len(df_display)), y=['preds', 'target'])
fig.write_html('handcrafted_model_viz_detailed.html')

# plot overview
display_days = 100
subsample = 90
df = pd.DataFrame({'preds': preds, 'target': y_test})
df_display = df[:display_days*17280:subsample]
fig = px.line(df_display, x=range(len(df_display)), y=['preds', 'target'])
fig.write_html('handcrafted_model_viz_overview.html')

# State to event
To go from event segmentation to state segmentation, we will find the median curve around both onset and wakeup events.
Given a new prediction, we shift this across the window with stride of 12, and measure the distance to the median curve, the similarity shows the likelihood of the event.

In [ ]:
# make preds for all data, both train and test
preds = clf.predict_proba(X)[:, 1]

In [ ]:
# find transitions in the target column (1=awake, 0=asleep)
diff = data.target.diff()
wakeups = diff[diff==1].index
onsets = diff[diff==-1].index

In [ ]:
# find the median curve of preds around each transition
window_size = 720

wakeup_curves = np.empty((len(wakeups), window_size))
for i, wakeup in enumerate(wakeups):
    left = wakeup - window_size//2
    right = wakeup + window_size//2
    wakeup_curves[i] = preds[left:right]
    
median_curve = np.median(wakeup_curves, axis=0)
mean_curve = np.mean(wakeup_curves, axis=0)

In [ ]:
# plot all the curves over each other
plt.figure(figsize=(20, 10))
plt.plot(wakeup_curves.T, alpha=0.1)
plt.title(f"Showing all {len(wakeups)} wakeup curves")
plt.axvline(window_size//2, color='black', linestyle='--')

# plot percentiles
for percentile in [10, 25, 50, 75, 90]:
    plt.plot(np.percentile(wakeup_curves, percentile, axis=0), label=f'{percentile}th percentile')

# plot mean
plt.plot(wakeup_curves.mean(axis=0), label='mean', color='black', linewidth=3)

plt.legend()
plt.show()

Let's show the response on a test series

In [ ]:
limit = 2500000
display_data = X_test[:limit]

display_preds = clf.predict_proba(display_data)[:, 1]

# normalize preds and median curve with std and mean
template = median_curve
# template = np.array([0]*(window_size//2)+[1]*(window_size//2))
template = template - template.mean()
display_preds = display_preds - template.mean()

result = np.correlate(display_preds, template, mode='valid')
result = np.pad(result, (window_size//2-1, window_size//2), 'constant', constant_values=0)
result = result / result.max()
result = result.clip(0, 1)

In [ ]:
# Plot the results
plot_df = pd.DataFrame({'preds': display_preds, 'result': result})
plot_df = plot_df[::36]
fig = px.line(plot_df, y=['preds', 'result'])

display_y = y_test[:limit].reset_index(drop=True)
display_wakeups = display_y[display_y.diff()==1].index
for display_wakeup in display_wakeups:
    fig.add_vline(x=display_wakeup, line_width=1, line_dash="dash", line_color="green")
fig.show()

In [ ]:
# iterate over display wakeups, look for the pred argmax within a window around the wakeup and compute the distance
dists = []
for display_wakeup in display_wakeups:
    tolerance = 500
    result_window = result[display_wakeup-tolerance:display_wakeup+tolerance]
    best_presult = result_window.argmax()
    dist = abs(best_presult - tolerance)
    dists.append(dist)
    
print(f"Mean distance: {np.mean(dists)}, median: {np.median(dists)}")

fig = plt.figure(figsize=(20, 5))
counts, bins, patches = plt.hist(dists, bins=500//12)
plt.xticks(bins)
plt.show()